In [1]:
from urllib.request import urlopen, Request
from bs4 import BeautifulSoup
from time import sleep
import csv
import re
import json
import time
import tqdm

In [2]:
# url to get artists
base_url_artists = "https://www.vagalume.com.br/browse/{}.html"

In [3]:
# Starting letters of the artists/bands
letters  = ["A", "B", "C", "D" , "E" , "F" , "G",  "H",  "I",  "J",  "K",  "L",  "M",  "N",  "O",  "P",  "Q",  "R",  "S",  "T",  "U",  "V",  "W",  "X",  "Y",  "Z",  "0-9"]
letters = [i.lower() for i in letters]

In [4]:
# To store the artist and it's link
# artist_links = []
# artist = []

# for letter in letters:
    
#     artist_url = base_url_artists.format(letter)
#     print("Going to url : ", artist_url)

#     # Reading the page data 
#     req = Request(artist_url, headers = {'User-Agent':'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:109.0) Gecko/20100101 Firefox/109.0'})
#     html_page = urlopen(req).read()
#     soup = BeautifulSoup(html_page, 'html.parser')
    
#     # Finding the required attributes
#     artist_list = soup.find('ul', class_="xsList2 smList4 mdList6 gridList", id="artTopsSection").find_all('a', href=True)
#     # Formatting and storing the information
#     for a in artist_list:
#         artist_links.append('https://www.vagalume.com.br' + a['href'])
#         artist.append(a.text)
#     time.sleep(1)
        


Going to url :  https://www.vagalume.com.br/browse/a.html
Going to url :  https://www.vagalume.com.br/browse/b.html
Going to url :  https://www.vagalume.com.br/browse/c.html
Going to url :  https://www.vagalume.com.br/browse/d.html
Going to url :  https://www.vagalume.com.br/browse/e.html
Going to url :  https://www.vagalume.com.br/browse/f.html
Going to url :  https://www.vagalume.com.br/browse/g.html
Going to url :  https://www.vagalume.com.br/browse/h.html
Going to url :  https://www.vagalume.com.br/browse/i.html
Going to url :  https://www.vagalume.com.br/browse/j.html
Going to url :  https://www.vagalume.com.br/browse/k.html
Going to url :  https://www.vagalume.com.br/browse/l.html
Going to url :  https://www.vagalume.com.br/browse/m.html
Going to url :  https://www.vagalume.com.br/browse/n.html
Going to url :  https://www.vagalume.com.br/browse/o.html
Going to url :  https://www.vagalume.com.br/browse/p.html
Going to url :  https://www.vagalume.com.br/browse/q.html
Going to url :

In [5]:
# Saving the artist links and artits
# Name of file to save to
# save_file = f"data/vagalume_data/artist_links.json"
# data = {'artist':artist,'links':artist_links}
# # open a file in write mode and save for each artist
# with open(save_file, "w") as f:
#     # write the dictionary to the file in JSON format
#     json.dump(data, f)

In [6]:
# Loading from file
file = f"data/vagalume_data/artist_links.json"
# open a file in write mode and save for each artist
with open(file) as f:
    data = json.load(f)

In [10]:
# Putting the data in the respective variable names
artist = data['artist']
artist_links = data['links']

In [11]:
# Testing 
# print(list(zip(artist_links,artist)))

In [19]:
# Storing the song dictionary
songs_dict = {} 

# Name of file to save to
t = int(time.time()*100)
save_file = f"data/vagalume_data/all_{t}.json"

counter = 0
for url, artst in tqdm.tqdm(zip(artist_links, artist)):
    
    # To prevent pulling the same data
    counter+=1
    if counter <=78:
        continue
    
    # Getting artist data
    print("Going to url : ", url)
    req = Request(url, headers={'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:109.0) Gecko/20100101 Firefox/109.0'})
    try:
        html_page = urlopen(req, timeout = 10).read()
    except Exception as e:
        print(e)
        print("Error at artist link")
        continue
        
    soup = BeautifulSoup(html_page, 'html.parser')
    
    # Genres of the artist
    genre_list = soup.find('div', class_="scrollable").find_all('a', href=True)
    genres_list = []
    for genre in genre_list:
        genres_list.append(genre.text)
    
    songs_dict[artst] = {'genres':genres_list, 'albums': []}
    
#     time.sleep(0.5)

    # Getting the popularity of the artist
    popularity_req = Request(url + "popularidade/", headers={'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:109.0) Gecko/20100101 Firefox/109.0'})
    try:
        popularity_html_page = urlopen(popularity_req, timeout = 10).read()
        popularity_soup = BeautifulSoup(popularity_html_page, 'html.parser')
        popularity = popularity_soup.find('ul', id='popFacts')
        
    except Exception as e:
        print(e)
        print("Error finding popularity")
        popularity = None
        

    
#     time.sleep(0.5)
    
    # Getting all the albums and songs of an artist
    albums_req = Request(url + "discografia/", headers={'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:109.0) Gecko/20100101 Firefox/109.0'})
    try:
        albums_html_page = urlopen(albums_req, timeout = 10).read()
    except Exception as e:
        print(e)
        print("Error getting albums page")
        continue
    
    albums_soup = BeautifulSoup(albums_html_page, 'html.parser')
    albums_list = albums_soup.find('div', class_='letrasWrapper').find_all('div', class_='cardAlbumInfos')
    all_songs_list = albums_soup.find_all('ol', id='topMusicList')
    
    albums_data = []
    # Iterating through each album and song to get the lyrics
    for idx,album in enumerate(albums_list):
        try:
            album_data = {
                            'albumTitle': album.find(re.compile('^h[1-6]$'), {'class': 'albumTitle'}).find('a').text,
                            'albumLink': album.find('a')['href'],
                            'albumYear': '',
                            'albumRecord': '',
                            'songs': []
                        }
        except Exception as e:
            print(e)
            print("Album list is not found")
            continue
        album_year_record = album.find('p', {'class': 'albumYear'}).get_text(separator='---')
        if '---' in album_year_record:
            album_data['albumYear'], album_data['albumRecord'] = album_year_record.split('---')
        else:
            album_data['albumYear'] = album_year_record.strip()
            album_data['albumRecord'] = ''
        
        # Getting the songs of the album
        songs_list = all_songs_list[idx]
        
        if songs_list:
            songs_list = songs_list.find_all('a', class_='nameMusic', href=True)
            count = len(songs_list)
            
            # Getting the lyrics of each song
            for song in songs_list:
                song_dict = {}
                song_dict['name'] = song.text
                print(f"Song name:{song.text}, Album:{album_data['albumTitle']}")
#                 time.sleep(0.5)
                song_dict['lyrics_link'] = 'https://www.vagalume.com.br' + song['href']
                req = Request(song_dict['lyrics_link'], headers = {'User-Agent':'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:109.0) Gecko/20100101 Firefox/109.0'})
                try:
                    html_page = urlopen(req, timeout = 10).read()
                    soup = BeautifulSoup(html_page, 'html.parser')
                    song_dict['lyrics'] = soup.find('div', id='lyrics').get_text(separator='. ').replace('<br/>', '\n')

                except Exception as e:
                    print(e)
                    song_dict['lyrics'] = None

                album_data['songs'].append(song_dict)

                
        else:
            print(f"No songs found for {artst}. Removing the url {url} from the list")
            artist_links.remove(url)
            artist.remove(artst)

        time.sleep(0.5)
        albums_data.append(album_data)
    

    songs_dict[artst]['albums'].append(albums_data)
    
    
    # open a file in write mode and save for each artist
    with open(save_file, "w") as f:
        # write the dictionary to the file in JSON format
        json.dump(songs_dict, f)
    
    
    
    
    
    
    

0it [00:00, ?it/s]

Going to url :  https://www.vagalume.com.br/alisson-neide/
Song name:Eu adoro, Album:Sinceridade
Song name:Aprender Com Jesus, Album:Sinceridade
Song name:Sinceridade, Album:Sinceridade
Song name:Paulo e silas, Album:Sinceridade
Song name:Dependente, Album:Sinceridade
Song name:Ele Veio e Virá, Album:Sinceridade
Song name:Qual é o Verdadeiro Jesus, Album:Sinceridade
Song name:Cante no Vale, Album:Sinceridade
Song name:Desce Com Pressa, Album:Sinceridade
Song name:A Viuva de Naim, Album:Sinceridade


79it [00:04, 17.82it/s]

Going to url :  https://www.vagalume.com.br/alice-cooper/
Song name:Rock & Roll, Album:Detroit Stories
Song name:Go Man Go, Album:Detroit Stories
Song name:Our Love Will Change the World, Album:Detroit Stories
Song name:Social Debris, Album:Detroit Stories
Song name:$1000 High Heel Shoes, Album:Detroit Stories
Song name:Hail Mary, Album:Detroit Stories
Song name:Detroit City 2021, Album:Detroit Stories
Song name:Drunk and in Love, Album:Detroit Stories
Song name:Independence Dave, Album:Detroit Stories
Song name:I Hate You, Album:Detroit Stories
Song name:Wonderful World, Album:Detroit Stories
Song name:Sister Anne, Album:Detroit Stories
Song name:Hanging On By a Thread (Don't Give Up), Album:Detroit Stories
Song name:Shut Up and Rock, Album:Detroit Stories
Song name:East Side Story, Album:Detroit Stories
Song name:Detroit City 2020, Album:Breadcrumbs (EP)
Song name:Go Man Go, Album:Breadcrumbs (EP)
Song name:East Side Story, Album:Breadcrumbs (EP)
Song name:Your Mama Won't Like Me, Al

79it [00:22, 17.82it/s]

...

<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
Going to url :  https://www.vagalume.com.br/5th-dimension/
<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
Going to url :  https://www.vagalume.com.br/5-a-seco/
<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
Going to url :  https://www.vagalume.com.br/311/


2133it [8:27:34, 14.11it/s]

<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
Going to url :  https://www.vagalume.com.br/38-special/
<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
Going to url :  https://www.vagalume.com.br/6lack/
<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
Going to url :  https://www.vagalume.com.br/509-e/


2136it [8:27:34, 14.26s/it]

<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
Going to url :  https://www.vagalume.com.br/2-chainz/
<urlopen error [Errno 11001] getaddrinfo failed>
Error at artist link
